In [2]:
from datasets import load_dataset, load_metric, Audio, Dataset
import os
import torchaudio
from tqdm.auto import tqdm

# Load English Data

In [94]:
common_voice_train = load_dataset('librispeech_asr', 'clean', split='train.100', use_auth_token=True)
common_voice_valid = load_dataset('librispeech_asr', 'clean', split='validation', use_auth_token=True)

Reusing dataset librispeech_asr (/workspace/.cache/huggingface/datasets/librispeech_asr/clean/2.1.0/8c6e15bda76db687d2a7c7198808151adecbb4d890ff463033a2e6f788c0ba25)
Reusing dataset librispeech_asr (/workspace/.cache/huggingface/datasets/librispeech_asr/clean/2.1.0/8c6e15bda76db687d2a7c7198808151adecbb4d890ff463033a2e6f788c0ba25)


In [95]:
common_voice_train = common_voice_train.remove_columns(["speaker_id", "chapter_id", "id"])
common_voice_valid = common_voice_valid.remove_columns(["speaker_id", "chapter_id", "id"])

In [96]:
common_voice_train[20]

{'file': '374-180298-0020.flac',
 'audio': {'path': '374-180298-0020.flac',
  'array': array([-0.00045776, -0.00015259,  0.00045776, ..., -0.00079346,
         -0.00082397, -0.00073242]),
  'sampling_rate': 16000},
 'text': 'I FLUNG MYSELF INTO THIS RAPID NOISY AND VOLCANIC LIFE WHICH HAD FORMERLY TERRIFIED ME WHEN I THOUGHT OF IT AND WHICH HAD BECOME FOR ME THE NECESSARY COMPLEMENT OF MY LOVE FOR MARGUERITE WHAT ELSE COULD I HAVE DONE'}

In [97]:
def normalize_text(batch):
    batch['sentence'] = batch['text'].lower()
    return batch

In [98]:
common_voice_train = common_voice_train.map(normalize_text, num_proc=32)
common_voice_valid = common_voice_valid.map(normalize_text, num_proc=32)

Loading cached processed dataset at /workspace/.cache/huggingface/datasets/librispeech_asr/clean/2.1.0/8c6e15bda76db687d2a7c7198808151adecbb4d890ff463033a2e6f788c0ba25/cache-39821e14da4ccfc6.arrow
Loading cached processed dataset at /workspace/.cache/huggingface/datasets/librispeech_asr/clean/2.1.0/8c6e15bda76db687d2a7c7198808151adecbb4d890ff463033a2e6f788c0ba25/cache-e4f620dfcf745abf.arrow
Loading cached processed dataset at /workspace/.cache/huggingface/datasets/librispeech_asr/clean/2.1.0/8c6e15bda76db687d2a7c7198808151adecbb4d890ff463033a2e6f788c0ba25/cache-3d1e276c48d7700d.arrow
Loading cached processed dataset at /workspace/.cache/huggingface/datasets/librispeech_asr/clean/2.1.0/8c6e15bda76db687d2a7c7198808151adecbb4d890ff463033a2e6f788c0ba25/cache-be0164e2ebe18904.arrow
Loading cached processed dataset at /workspace/.cache/huggingface/datasets/librispeech_asr/clean/2.1.0/8c6e15bda76db687d2a7c7198808151adecbb4d890ff463033a2e6f788c0ba25/cache-7ae9fcac3a3f91a6.arrow
Loading cached 

In [99]:
common_voice_train[11]

{'file': '374-180298-0011.flac',
 'audio': {'path': '374-180298-0011.flac',
  'array': array([-1.52587891e-04, -3.05175781e-05,  3.05175781e-05, ...,
         -3.96728516e-04,  1.28173828e-03,  1.09863281e-03]),
  'sampling_rate': 16000},
 'text': 'FORGIVE ME IF I GIVE YOU ALL THESE DETAILS BUT YOU WILL SEE THAT THEY WERE THE CAUSE OF WHAT WAS TO FOLLOW WHAT I TELL YOU IS A TRUE AND SIMPLE STORY AND I LEAVE TO IT ALL THE NAIVETE OF ITS DETAILS',
 'sentence': 'forgive me if i give you all these details but you will see that they were the cause of what was to follow what i tell you is a true and simple story and i leave to it all the naivete of its details'}

### Clean Up the Text

In [100]:
# Remove character
import re
chars_to_remove_regex = '[\,\?\.\!\-\;\:\"\“\%\‘\”\�\'\。]'
def remove_special_characters(batch):
    sentence = re.sub(chars_to_remove_regex, '', batch["sentence"])
    batch['sentence'] = sentence
    return batch

In [101]:
common_voice_train = common_voice_train.map(remove_special_characters, num_proc=16)
common_voice_valid = common_voice_valid.map(remove_special_characters, num_proc=16)

Loading cached processed dataset at /workspace/.cache/huggingface/datasets/librispeech_asr/clean/2.1.0/8c6e15bda76db687d2a7c7198808151adecbb4d890ff463033a2e6f788c0ba25/cache-e4a181970b0ccf3a.arrow
Loading cached processed dataset at /workspace/.cache/huggingface/datasets/librispeech_asr/clean/2.1.0/8c6e15bda76db687d2a7c7198808151adecbb4d890ff463033a2e6f788c0ba25/cache-366a9a8ad0d4f020.arrow
Loading cached processed dataset at /workspace/.cache/huggingface/datasets/librispeech_asr/clean/2.1.0/8c6e15bda76db687d2a7c7198808151adecbb4d890ff463033a2e6f788c0ba25/cache-9c81fa6805a57e36.arrow
Loading cached processed dataset at /workspace/.cache/huggingface/datasets/librispeech_asr/clean/2.1.0/8c6e15bda76db687d2a7c7198808151adecbb4d890ff463033a2e6f788c0ba25/cache-98662e2e0d6de08c.arrow
Loading cached processed dataset at /workspace/.cache/huggingface/datasets/librispeech_asr/clean/2.1.0/8c6e15bda76db687d2a7c7198808151adecbb4d890ff463033a2e6f788c0ba25/cache-2ed4f597158e7f97.arrow
Loading cached 

In [102]:
common_voice_train[1]

{'file': '374-180298-0001.flac',
 'audio': {'path': '374-180298-0001.flac',
  'array': array([-9.15527344e-05, -1.52587891e-04, -1.52587891e-04, ...,
         -2.13623047e-04, -1.83105469e-04, -2.74658203e-04]),
  'sampling_rate': 16000},
 'text': "MARGUERITE TO BE UNABLE TO LIVE APART FROM ME IT WAS THE DAY AFTER THE EVENING WHEN SHE CAME TO SEE ME THAT I SENT HER MANON LESCAUT FROM THAT TIME SEEING THAT I COULD NOT CHANGE MY MISTRESS'S LIFE I CHANGED MY OWN",
 'sentence': 'marguerite to be unable to live apart from me it was the day after the evening when she came to see me that i sent her manon lescaut from that time seeing that i could not change my mistresss life i changed my own'}

### Build Character

In [103]:
vocab_train = []
vocab_test  = []

for batch in tqdm(common_voice_train):
    sentence = batch['sentence']
    vocab_train.extend(list(set(list(sentence))))
    
for batch in tqdm(common_voice_valid):
    sentence = batch['sentence']
    vocab_test.extend(list(set(list(sentence))))

  0%|          | 0/28539 [00:00<?, ?it/s]

  0%|          | 0/2703 [00:00<?, ?it/s]

In [104]:
vocab_list = list(set(vocab_train) | set(vocab_test))
vocab_dict = {v: k for k, v in enumerate(sorted(vocab_list))}

In [105]:
print(vocab_dict)

{' ': 0, 'a': 1, 'b': 2, 'c': 3, 'd': 4, 'e': 5, 'f': 6, 'g': 7, 'h': 8, 'i': 9, 'j': 10, 'k': 11, 'l': 12, 'm': 13, 'n': 14, 'o': 15, 'p': 16, 'q': 17, 'r': 18, 's': 19, 't': 20, 'u': 21, 'v': 22, 'w': 23, 'x': 24, 'y': 25, 'z': 26}


In [106]:
# make the space more intuitive to understand
vocab_dict["|"] = vocab_dict[" "]
del vocab_dict[" "]

vocab_dict["[UNK]"] = len(vocab_dict)
vocab_dict["[PAD]"] = len(vocab_dict)
len(vocab_dict)

29

In [107]:
print(vocab_dict)

{'a': 1, 'b': 2, 'c': 3, 'd': 4, 'e': 5, 'f': 6, 'g': 7, 'h': 8, 'i': 9, 'j': 10, 'k': 11, 'l': 12, 'm': 13, 'n': 14, 'o': 15, 'p': 16, 'q': 17, 'r': 18, 's': 19, 't': 20, 'u': 21, 'v': 22, 'w': 23, 'x': 24, 'y': 25, 'z': 26, '|': 0, '[UNK]': 27, '[PAD]': 28}


In [108]:
import json
with open('vocab.json', 'w') as vocab_file:
    json.dump(vocab_dict, vocab_file)

# Tokenizer

In [109]:
from transformers import Wav2Vec2CTCTokenizer
from transformers import Wav2Vec2FeatureExtractor
from transformers import Wav2Vec2Processor

In [110]:
tokenizer = Wav2Vec2CTCTokenizer.from_pretrained("./", unk_token="[UNK]", pad_token="[PAD]", word_delimiter_token="|")  # './' load vocab.json in the current directory
feature_extractor = Wav2Vec2FeatureExtractor(feature_size=1, sampling_rate=16000, padding_value=0.0, do_normalize=True, return_attention_mask=True)  
processor = Wav2Vec2Processor(feature_extractor=feature_extractor, tokenizer=tokenizer)

file ./config.json not found
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [26]:
# def speech_file_to_array_fn(batch):
#     audio_array, sampling_rate = torchaudio.load(batch["path"])
#     batch["audio"] = {
#         "array": audio_array[0].numpy(),
#         "path": batch["path"],
#         "sampling_rate": sampling_rate
#     }
#     return batch

In [27]:
# common_voice_train = common_voice_train.map(speech_file_to_array_fn)
# common_voice_test = common_voice_test.map(speech_file_to_array_fn)

0ex [00:00, ?ex/s]

0ex [00:00, ?ex/s]

In [111]:
common_voice_train  = common_voice_train.cast_column("audio", Audio(sampling_rate=16_000))
common_voice_valid  = common_voice_valid.cast_column("audio", Audio(sampling_rate=16_000))

In [38]:
# common_voice_train = common_voice_train.cast_column("path", Audio(sampling_rate=16_000)).rename_column('path', 'audio')
# common_voice_valid  = common_voice_valid.cast_column("path", Audio(sampling_rate=16_000)).rename_column('path', 'audio')

In [112]:
common_voice_train[0]

{'file': '374-180298-0000.flac',
 'audio': {'path': '374-180298-0000.flac',
  'array': array([ 7.01904297e-04,  7.32421875e-04,  7.32421875e-04, ...,
         -2.74658203e-04, -1.83105469e-04, -3.05175781e-05]),
  'sampling_rate': 16000},
 'text': 'CHAPTER SIXTEEN I MIGHT HAVE TOLD YOU OF THE BEGINNING OF THIS LIAISON IN A FEW LINES BUT I WANTED YOU TO SEE EVERY STEP BY WHICH WE CAME I TO AGREE TO WHATEVER MARGUERITE WISHED',
 'sentence': 'chapter sixteen i might have told you of the beginning of this liaison in a few lines but i wanted you to see every step by which we came i to agree to whatever marguerite wished'}

In [113]:
import IPython.display as ipd
import numpy as np
import random

rand_int = random.randint(0, len(common_voice_train)-1)

print("Target text:", common_voice_train[rand_int]["sentence"])
print("Input array shape:", common_voice_train[rand_int]["audio"]["array"].shape)
print("Sampling rate:", common_voice_train[rand_int]["audio"]["sampling_rate"])
ipd.Audio(data=common_voice_train[rand_int]["audio"]["array"], autoplay=False, rate=16000)

Target text: are derived from a radical signifying white
Input array shape: (69360,)
Sampling rate: 16000


In [114]:
# This does not prepare the input for the Transformer model.
# This will resample the data and convert the sentence into indices
# Batch here is just for one entry (row)
def prepare_dataset(batch):
    audio = batch["audio"]
    
    # batched output is "un-batched"
    batch["input_values"] = processor(audio["array"], sampling_rate=audio["sampling_rate"]).input_values[0]
    batch["input_length"] = len(batch["input_values"])
    
    with processor.as_target_processor():
        batch["labels"] = processor(batch["sentence"]).input_ids
    return batch

In [115]:
common_voice_train = common_voice_train.map(prepare_dataset, remove_columns=common_voice_train.column_names)
common_voice_valid = common_voice_valid.map(prepare_dataset, remove_columns=common_voice_valid.column_names)

0ex [00:00, ?ex/s]

Loading cached processed dataset at /workspace/.cache/huggingface/datasets/librispeech_asr/clean/2.1.0/8c6e15bda76db687d2a7c7198808151adecbb4d890ff463033a2e6f788c0ba25/cache-440d93538cd91d0a.arrow


In [117]:
# In case the dataset is too long which can lead to OOM. We should filter them out.
max_input_length_in_sec = 8.0
common_voice_train = common_voice_train.filter(lambda x: x < max_input_length_in_sec * processor.feature_extractor.sampling_rate, input_columns=["input_length"])
common_voice_valid = common_voice_valid.filter(lambda x: x < max_input_length_in_sec * processor.feature_extractor.sampling_rate, input_columns=["input_length"])

  0%|          | 0/29 [00:00<?, ?ba/s]

  0%|          | 0/3 [00:00<?, ?ba/s]

In [118]:
import torch

from dataclasses import dataclass, field
from typing import Any, Dict, List, Optional, Union

@dataclass
class DataCollatorCTCWithPadding:
    """
    Data collator that will dynamically pad the inputs received.
    Args:
        processor (:class:`~transformers.Wav2Vec2Processor`)
            The processor used for proccessing the data.
        padding (:obj:`bool`, :obj:`str` or :class:`~transformers.tokenization_utils_base.PaddingStrategy`, `optional`, defaults to :obj:`True`):
            Select a strategy to pad the returned sequences (according to the model's padding side and padding index)
            among:
            * :obj:`True` or :obj:`'longest'`: Pad to the longest sequence in the batch (or no padding if only a single
              sequence if provided).
            * :obj:`'max_length'`: Pad to a maximum length specified with the argument :obj:`max_length` or to the
              maximum acceptable input length for the model if that argument is not provided.
            * :obj:`False` or :obj:`'do_not_pad'` (default): No padding (i.e., can output a batch with sequences of
              different lengths).
    """

    processor: Wav2Vec2Processor
    padding: Union[bool, str] = True

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lenghts and need
        # different padding methods
        input_features = [{"input_values": feature["input_values"]} for feature in features]
        label_features = [{"input_ids": feature["labels"]} for feature in features]

        batch = self.processor.pad(
            input_features,
            padding=self.padding,
            return_tensors="pt",
        )

        with self.processor.as_target_processor():
            labels_batch = self.processor.pad(
                label_features,
                padding=self.padding,
                return_tensors="pt",
            )

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        batch["labels"] = labels

        return batch

In [119]:
data_collator = DataCollatorCTCWithPadding(processor=processor, padding=True)

In [120]:
wer_metric = load_metric("wer")
# cer_metric = load_metric("cer")

In [121]:
def compute_metrics(pred):
    pred_logits = pred.predictions
    pred_ids = np.argmax(pred_logits, axis=-1)

    pred.label_ids[pred.label_ids == -100] = tokenizer.pad_token_id

    pred_str = tokenizer.batch_decode(pred_ids)
    label_str = tokenizer.batch_decode(pred.label_ids, group_tokens=False)
    
    wer = wer_metric.compute(predictions=pred_str, references=label_str)
#     cer = cer_metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer}
#     return {"cer": cer}

In [142]:
from transformers import Wav2Vec2ForCTC

model = Wav2Vec2ForCTC.from_pretrained(
    "facebook/wav2vec2-xls-r-300m", 
    attention_dropout=0.1,
    layerdrop=0.0,
    feat_proj_dropout=0.0,
    mask_time_prob=0.75, 
    mask_time_length=10,
    mask_feature_prob=0.25,
    mask_feature_length=64,
    ctc_loss_reduction="mean",
    pad_token_id=processor.tokenizer.pad_token_id,
    vocab_size=len(processor.tokenizer)
)

loading configuration file https://huggingface.co/facebook/wav2vec2-xls-r-300m/resolve/main/config.json from cache at /workspace/.cache/huggingface/transformers/dabc27df63e37bd2a7a221c7774e35f36a280fbdf917cf54cadfc7df8c786f6f.a3e4c3c967d9985881e0ae550a5f6f668f897db5ab2e0802f9b97973b15970e6
Model config Wav2Vec2Config {
  "activation_dropout": 0.0,
  "adapter_kernel_size": 3,
  "adapter_stride": 2,
  "add_adapter": false,
  "apply_spec_augment": true,
  "architectures": [
    "Wav2Vec2ForPreTraining"
  ],
  "attention_dropout": 0.1,
  "bos_token_id": 1,
  "classifier_proj_size": 256,
  "codevector_dim": 768,
  "contrastive_logits_temperature": 0.1,
  "conv_bias": true,
  "conv_dim": [
    512,
    512,
    512,
    512,
    512,
    512,
    512
  ],
  "conv_kernel": [
    10,
    3,
    3,
    3,
    3,
    2,
    2
  ],
  "conv_stride": [
    5,
    2,
    2,
    2,
    2,
    2,
    2
  ],
  "ctc_loss_reduction": "mean",
  "ctc_zero_infinity": false,
  "diversity_loss_weight": 0.1,
 

In [143]:
model.freeze_feature_encoder()

In [147]:
from transformers import TrainingArguments

training_args = TrainingArguments(
  output_dir='.',
  group_by_length=True,
  per_device_train_batch_size=8,
  gradient_accumulation_steps=4,
  evaluation_strategy="steps",
  gradient_checkpointing=True,
  fp16=True,
  num_train_epochs=50,
  save_steps=500,
  eval_steps=500,
  logging_steps=100,
  learning_rate=5e-5,
  warmup_steps=1000,
  save_total_limit=3,
  load_best_model_at_end=True
)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).


In [148]:
from transformers import Trainer

trainer = Trainer(
    model=model,
    data_collator=data_collator,
    args=training_args,
    compute_metrics=compute_metrics,
    train_dataset=common_voice_train,
    eval_dataset=common_voice_valid,
    tokenizer=processor.feature_extractor,
)

Using amp half precision backend


In [149]:
trainer.train()

The following columns in the training set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
/opt/conda/lib/python3.8/site-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use thePyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
***** Running training *****
  Num examples = 3857
  Num Epochs = 50
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 32
  Gradient Accumulation steps = 4
  Total optimization steps = 6000


The following columns in the evaluation set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
***** Running Evaluation *****
  Num examples = 1812
  Batch size = 8
Saving model checkpoint to ./checkpoint-500
Configuration saved in ./checkpoint-500/config.json
Model weights saved in ./checkpoint-500/pytorch_model.bin
Configuration saved in ./checkpoint-500/preprocessor_config.json
The following columns in the evaluation set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
***** Running Evaluation *****
  Num examples = 1812
  Batch size = 8
Saving model checkpoint to ./checkpoint-1000
Configuration saved in ./checkpoint-1000/config.json
Model weights saved in ./checkpoint-1000/pytorch_model.bin
Configuration saved in ./checkpoint-1000/preprocessor_config.json
The following columns in the evaluation set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ign

TrainOutput(global_step=6000, training_loss=1.1765391832987468, metrics={'train_runtime': 14177.2496, 'train_samples_per_second': 13.603, 'train_steps_per_second': 0.423, 'total_flos': 2.9510893171822916e+19, 'train_loss': 1.1765391832987468, 'epoch': 49.99})

In [150]:
tokenizer.save_pretrained('.')

tokenizer config file saved in ./tokenizer_config.json
Special tokens file saved in ./special_tokens_map.json
added tokens file saved in ./added_tokens.json


('./tokenizer_config.json',
 './special_tokens_map.json',
 './vocab.json',
 './added_tokens.json')

In [151]:
processor.save_pretrained('.')

Configuration saved in ./preprocessor_config.json
tokenizer config file saved in ./tokenizer_config.json
Special tokens file saved in ./special_tokens_map.json
added tokens file saved in ./added_tokens.json


In [152]:
kwargs = {
    "finetuned_from": "facebook/wav2vec2-xls-r-300m",
    "tasks": "speech-recognition",
    "tags": ["automatic-speech-recognition", "librispeech_asr", "robust-speech-event", "en"],
    "dataset_args": f"Config: clean, Training split: train.100, Eval split: validation",
    "dataset": "librispeech_asr",
    "language": "en"
}

In [153]:
trainer.create_model_card(**kwargs)

Dropping the following result as it does not have all the necessary fields:
{}


In [154]:
trainer.save_model('.')

Saving model checkpoint to .
Configuration saved in ./config.json
Model weights saved in ./pytorch_model.bin
Configuration saved in ./preprocessor_config.json


In [ ]:
tokenizer.push_to_hub('.')

In [61]:
model.push_to_hub('vitouphy/xls-r-300m-ja')

Configuration saved in vitouphy/xls-r-300m-ja/config.json
Model weights saved in vitouphy/xls-r-300m-ja/pytorch_model.bin


Upload file pytorch_model.bin:   0%|          | 3.39k/1.18G [00:00<?, ?B/s]

To https://huggingface.co/vitouphy/xls-r-300m-ja
   b5d6daa..1e678ca  main -> main



'https://huggingface.co/vitouphy/xls-r-300m-ja/commit/1e678ca0c4b03aa3bca71af6fd2c0aa738b7aa7b'

In [62]:
1

1

In [57]:
trainer.push_to_hub('vitouphy/xls-r-300m-ja')

Saving model checkpoint to .
Configuration saved in ./config.json
Model weights saved in ./pytorch_model.bin
Configuration saved in ./preprocessor_config.json


AttributeError: 'Trainer' object has no attribute 'repo'